In [1]:
import os
os.environ["CALITP_BQ_MAX_BYTES"] = str(800_000_000_000)
os.environ['USE_PYGEOS'] = '0'
import shared_utils

from calitp_data_analysis.tables import tbls
import calitp_data_analysis.magics
from calitp_data.storage import get_fs

from siuba import *
import pandas as pd
import geopandas as gpd

import datetime as dt

In [2]:
import segment_speed_utils

In [3]:
analysis_date = dt.date(2023, 4, 12)

In [4]:
fs = get_fs()

In [5]:
# path = 'gs://calitp-analytics-data/data-analyses/rt_segment_speeds/export/avg_speeds_stop_segments_2023-04-12.parquet'

In [6]:
# fs.get(path, './avg_speeds_stop_segments_2023-04-12.parquet')

In [7]:
exported_segments = pd.read_parquet('./avg_speeds_stop_segments_2023-04-12.parquet')

In [8]:
exported_segments >> head(1)

org_id                            agency_name   shape_id  \
0  recOZgevYf7Jimm9L  Alameda-Contra Costa Transit District  shp-10-09   

   stop_sequence stop_id                                           geometry  \
0              2   55050  b'\x01\x02\x00\x00\x00\x1d\x00\x00\x00Q\x86\xb...   

   p50_mph  p20_mph  p80_mph  n_trips time_of_day  \
0     2.19     1.75     3.13       63     all_day   

                                          base64_url  district  \
0  aHR0cHM6Ly9hcGkuNTExLm9yZy90cmFuc2l0L3ZlaGljbG...         4   

          district_name  
0  District 4 - Oakland

In [9]:
gdf = gpd.GeoDataFrame(exported_segments,
                 geometry=gpd.GeoSeries.from_wkb(exported_segments.geometry),
                 crs=segment_speed_utils.project_vars.PROJECT_CRS
                )

In [10]:
gdf >> head(3)

org_id                            agency_name   shape_id  \
0  recOZgevYf7Jimm9L  Alameda-Contra Costa Transit District  shp-10-09   
1  recOZgevYf7Jimm9L  Alameda-Contra Costa Transit District  shp-10-09   
2  recOZgevYf7Jimm9L  Alameda-Contra Costa Transit District  shp-10-09   

   stop_sequence stop_id                                           geometry  \
0              2   55050  LINESTRING (-183825.823 -36469.556, -183825.82...   
1              2   55050  LINESTRING (-183825.823 -36469.556, -183825.82...   
2              3   51207  LINESTRING (-183469.198 -36386.667, -183469.19...   

   p50_mph  p20_mph  p80_mph  n_trips time_of_day  \
0     2.19     1.75     3.13       63     all_day   
1     2.20     1.71     2.41       24        peak   
2    10.08     7.09    16.05       61     all_day   

                                          base64_url  district  \
0  aHR0cHM6Ly9hcGkuNTExLm9yZy90cmFuc2l0L3ZlaGljbG...         4   
1  aHR0cHM6Ly9hcGkuNTExLm9yZy90cmFuc2l0L3ZlaGljbG...         4   
2  aHR0cHM6Ly9hcGkuNTExLm9yZy90cmFuc2l0L3ZlaGljbG...         4   

          district_name  
0  District 4 - Oakland  
1  District 4 - Oakland  
2  District 4 - Oakland

In [11]:
# opening direct from gcs seemed to hang?
# gpd.read_file('./avg_speeds_stop_segments_2023-04-12.parquet')

In [12]:
shared_utils.rt_utils.get_speedmaps_ix_df?

Signature:
shared_utils.rt_utils.get_speedmaps_ix_df(
    analysis_date: datetime.date,
    itp_id: Optional[int] = None,
) -> pandas.core.frame.DataFrame
Docstring:
Collect relevant keys for finding all schedule and rt data for a reports-assessed organization.
Note that organizations may have multiple sets of feeds, or share feeds with other orgs.

Used with specific itp_id in rt_analysis.rt_parser.OperatorDayAnalysis, or without specifying itp_id
to get an overall table of which datasets were processed and how to deduplicate if needed
File:      ~/data-analyses/_shared_utils/shared_utils/rt_utils.py
Type:      function

In [13]:
shared_utils.rt_utils.get_speedmaps_ix_df(analysis_date) >> filter(_.organization_name.str.contains('Santa')) >> head(1)

feed_key         schedule_gtfs_dataset_key  \
23  199d652b518af1f2aef47e9c3c4f82e0  de792182088eecc3d5c0bd3f1df62965   

   vehicle_positions_gtfs_dataset_key  organization_itp_id  \
23   33dd64366cfab802596d05a407a4a35a                  293   

       caltrans_district                            organization_name  \
23  05 - San Luis Obispo  Santa Barbara Metropolitan Transit District   

   service_date  
23   2023-04-12

In [14]:
sc_url = (tbls.mart_transit_database.dim_gtfs_datasets()
          >> filter(_.key == 'ccc3d54df8d5cd4de797301968423d23')
          >> collect()
         ).base64_url.iloc[0]

In [15]:
segments_santa = gdf >> filter(_.time_of_day == 'all_day', _.base64_url == sc_url)

In [16]:
segments_santa.explore()

In [17]:
## TODO this on an SPA map... 

In [18]:
from rt_analysis import rt_filter_map_plot

In [19]:
rt_day = rt_filter_map_plot.from_gcs(296, analysis_date)

found shapes parquet at gs://calitp-analytics-data/data-analyses/rt_delay/v2_cached_views/shapes_296_2023-04-12.parquet


In [20]:
_m = rt_day.segment_speed_map(no_render=True)

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:445: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:445: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [21]:
rt_day.map_gz_export()

writing to calitp-map-tiles/speeds_2023-04-12/05_SHN.geojson.gz
writing to calitp-map-tiles/speeds_2023-04-12/296_All_Day_speeds.geojson.gz


In [24]:
rt_day.display_spa_map()